In [1]:
import numpy as np
import xarray

import matplotlib as mpl
from matplotlib import pyplot as plt

import netCDF4
from netCDF4 import Dataset

from bokeh.plotting import figure, output_notebook, show
output_notebook()
from IPython.display import IFrame

YEAR = 8766 # One year is 8766 hours
DATETIME_FMT = "%Y-%m-%d %H:%M"

/Users/nagydaniel/anaconda3/lib/python3.7/site-packages/dask/config.py:168: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  data = yaml.load(f.read()) or {}
/Users/nagydaniel/anaconda3/lib/python3.7/site-packages/distributed/config.py:20: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  defaults = yaml.load(f)


Loading BokehJS ...

In [2]:
ds = Dataset("./data/ERA5-hourly-merged.nc")

In [3]:
ds.variables['time']

<class 'netCDF4._netCDF4.Variable'>
int64 time(time)
    units: hours
    long_name: hours since 1900-01-01 00:00:00.0 minus 692496
unlimited dimensions: 
current shape = (201624,)
filling on, default _FillValue of -9223372036854775806 used

In [4]:
long = np.array(ds.variables['longitude'])
lat = np.array(ds.variables['latitude'])
hours = np.array(ds.variables['time'])
t2m = np.array(ds.variables['t2m'])
skt = np.array(ds.variables['skt'])
stl1 = np.array(ds.variables['stl1'])
stl2 = np.array(ds.variables['stl2'])

# the relevant data is stl2[0][0]
temps = np.array([x[0][0] for x in stl2]).astype(float)

In [5]:
# Plot the 16 weather parameters in function of time
# opts = dict(plot_width=900, plot_height=250, min_border=0)
# p = figure(**opts)



# r = p.line(hours, [x[0][0] for x in t2m], color='blue', alpha=0.6)
# r2 = p.line(hours, [x[0][1] for x in t2m], color='red', alpha=0.6)

# r = p.line(hours, temps)
# show(p)

In [6]:
hours[-1]//YEAR, hours[-1]%YEAR

(23, 5)

In [7]:
from datetime import datetime
from datetime import timezone

def datetimeToHour(dt):
    ts_null = datetime.strptime('1900-01-01 00:00', DATETIME_FMT).replace(tzinfo=timezone.utc).timestamp()
    ts_dt = datetime.strptime(dt, DATETIME_FMT).replace(tzinfo=timezone.utc).timestamp()
    return int((ts_dt-ts_null)//3600-692496)
datetimeToHour = np.vectorize(datetimeToHour)

def hourToTimestamp(h):
    ts_null = datetime.strptime('1900-01-01 00:00', DATETIME_FMT).replace(tzinfo=timezone.utc).timestamp()
    ts_date = int(ts_null) + 692496*3600 + 3600*h
    return ts_date
hourToTimestamp = np.vectorize(hourToTimestamp)

def hourToUTC(h):
    ts = hourToTimestamp(h)
    return datetime.utcfromtimestamp(ts)
hourToUTC = np.vectorize(hourToUTC)

def hourToUTCFormatted(h):
    return hourToUTC(h).strftime(DATETIME_FMT)
hourToUTCFormatted = np.vectorize(hourToUTCFormatted)

def getYearBeforeDateTime(dt):
    hr = datetimeToHour(dt)
    hr_start = hr-YEAR
    return slice(hr_start, hr)

def getYearBeforeTimestamp(ts):
    pass

# Report II on flowering prediction
## Nagy Dániel

In [12]:
# Plot one year
opts = dict(plot_width=900, plot_height=350, min_border=0, x_axis_type='datetime')
p = figure(**opts)

from bokeh.models import DatetimeTickFormatter
p.xaxis.formatter=DatetimeTickFormatter(
        hours=["%d %B %Y"],
        days=["%d %B %Y"],
        months=["%d %B %Y"],
        years=["%d %B %Y"],
)
p.xaxis.major_label_orientation = np.pi/4
p.xaxis.axis_label = 'Date'
p.yaxis.axis_label = 'Temperature soil 2 [K]'
r = p.line(hourToUTC(hours), temps)

In [13]:
show(p)

<img src="images/bokeh_plot-2.png"></img>

In [10]:
# Plot one year
opts = dict(plot_width=900, plot_height=350, min_border=0, x_axis_type='datetime')
p = figure(**opts)

from bokeh.models import DatetimeTickFormatter
p.xaxis.formatter=DatetimeTickFormatter(
        hours=["%d %B %Y"],
        days=["%d %B %Y"],
        months=["%d %B %Y"],
        years=["%d %B %Y"],
)
p.xaxis.major_label_orientation = np.pi/4
p.xaxis.axis_label = 'Date'
p.yaxis.axis_label = 'Temperature soil 2 [K]'
slc = getYearBeforeDateTime('1998-10-11 00:00')
r = p.line(hourToUTC(hours[slc]), temps[slc], legend="1998")

slc2 = getYearBeforeDateTime('1997-10-11 00:00')
r2 = p.line(hourToUTC(hours[slc2]), temps[slc2], color='red', legend="1997")

In [11]:
show(p)

<img src="images/bokeh_plot.png"></img>

# Implementing the LSCD Model

- The LSCD model is a mathematical model that aims to describe how plants sense winter cold and how they decide the correct time for flowering.
- [Article by Kourounioti, Hepworth, et. al.](https://www.sciencedirect.com/science/article/pii/S2405471218304368)
- The key is the spliced and unspliced VERNALIZATION INSENSITIVE3 (VIN3) mRNA concentration
- The plant can measure the concentration of VIN3 and sVIN3 across multiple timescales:
- L(Long term), S(Short term), C(Current), D(Diurnal)
- The LSCD model is a mathematical model that consists of a system of differential equations describing the concentration of the spliced and unspliced VIN3

# Long term: increases slowly in the cold $(<17^{\circ}C)$ and decreases slowly in the warm.

<img src="images/param_L.png"></img>

# Short term: remembers the presence of a high temperature spike until the evening and, during that time, remains decreased.

<img src="images/param_S.png"></img>

# Current term: high at low temperatures and low at high temperatures, changing linearly with temperature between $8^{\circ}C$ and $15.4^{\circ}C$.

<img src="images/param_C.png"></img>

# Diurnal term: cycles each day, peaking in the afternoon.

<img src="images/param_D.png"></img>

# The system of equations in the LSCD model

- The unspliced VIN3 concentration is denoted with $\nu$
- The spliced VIN3 concentration is denoted with V
$$
\begin{equation*}
\frac{\mathrm d\nu}{\mathrm d t} = p_{\nu}(L, S, C, D) - s_{\nu}\nu\\
\frac{\mathrm dV}{\mathrm dt} = s_{\nu}\nu - d_VV
\end{equation*}
$$
- Here, $p_{\nu}(L, S, C, D)=LSCD$ is the productive transcription, $s_{\nu}$ is the splicing rate, and $d_V$ is the degradation rate of the spliced VIN3.

$$
\begin{equation*}
\frac{\mathrm dL}{\mathrm dt} =
\begin{cases}
1-d_LL & T < T_L \\
-d_LL & T \geq T_L
\end{cases}
\end{equation*}
$$

$$
\begin{equation*}
C(T) =
\begin{cases}
p_{c1} & T \leq T_{c1} \\
p_{c1}-p_{c2}\frac{T-T_{c1}}{T_{c2}-T_{c1}} & T_{c1} < T < T_{c2} \\
p_{c2} & T \geq T_{c2}
\end{cases}
\end{equation*}
$$

$$
\begin{equation*}
S(T_m) = 
\begin{cases}
1, & T < T_S \\
S_1, & T \geq T_S
\end{cases}
\end{equation*}
$$

$$
\begin{equation*}
D(t) =  \left[p_D + \sin\left(2\pi\left(t - \frac{t_m-1}{24}\right)\right)\right]^2
\end{equation*}
$$
- $T_m$ is the maximum temperature since the last resetting, which was chosen to occur each day at 4pm.
- $t_m$ is the time at dawn.

# Fittable parameters of the model
| param     | dimension | value in the article |
|:---------:|-----------|----------------------|
| $d_V$     | day$^{-1}$| 18 |
| $s_{\nu}$ | day$^{-1}$|4.4$d_V$|
| $S_1$     | 1 | 0.75 |
| $T_L$     | $^{\circ}$C | 17 |
| $d_L$     | day$^{-1}$| 0.009 |
| $T_{c1}$  | $^{\circ}$C | 8 |
| $T_{c2}$  | $^{\circ}$C | 15.4 |
| $p_{c1}$  | 1 | 0.0315 |
| $p_{c2}$  | 1 | 0.03   |
| $p_D$     | 1 | 2.05 |
| $T_S$     | $^{\circ}$C | 15 |

# Thank You for attention!